In [14]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, count, avg, desc
import pymongo
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report

In [ ]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, count, avg, desc
import pymongo
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report

# Création de la session Spark
spark = SparkSession.builder \
    .appName("MongoDB_Analysis") \
    .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:10.4.1") \
    .config("spark.mongodb.read.connection.uri", "mongodb://mongodb:27017/github_issues") \
    .getOrCreate()

# Lecture des issues depuis MongoDB
df_issues = spark.read.format("mongodb") \
    .option("database", "github_issues") \
    .option("collection", "closed_issues") \
    .load()

# Afficher un aperçu des données
df_issues.show(5)

# Compter le nombre total d'issues
issue_count = df_issues.count()
print(f"Nombre total d'issues: {issue_count}")

# Nombre d'issues par langage
df_language_count = df_issues.groupBy("language").agg(count("issue_id").alias("count")).orderBy(desc("count"))
df_language_count.show()

# Durée moyenne de fermeture des issues par langage
df_duration_avg = df_issues.groupBy("language").agg(avg("duration").alias("avg_duration")).orderBy(desc("avg_duration"))
df_duration_avg.show()

# Arrêter la session Spark
spark.stop()


:: loading settings :: url = jar:file:/opt/bitnami/spark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /root/.ivy2/cache
The jars for the packages stored in: /root/.ivy2/jars
org.mongodb.spark#mongo-spark-connector_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-9166260b-a39a-48fa-a00f-491d46a19225;1.0
	confs: [default]
	found org.mongodb.spark#mongo-spark-connector_2.12;10.4.1 in central
	found org.mongodb#mongodb-driver-sync;5.1.4 in central
	[5.1.4] org.mongodb#mongodb-driver-sync;[5.1.1,5.1.99)
	found org.mongodb#bson;5.1.4 in central
	found org.mongodb#mongodb-driver-core;5.1.4 in central
	found org.mongodb#bson-record-codec;5.1.4 in central
:: resolution report :: resolve 1870ms :: artifacts dl 11ms
	:: modules in use:
	org.mongodb#bson;5.1.4 from central in [default]
	org.mongodb#bson-record-codec;5.1.4 from central in [default]
	org.mongodb#mongodb-driver-core;5.1.4 from central in [default]
	org.mongodb#mongodb-driver-sync;5.1.4 from central in [default]
	org.mongodb.spark#mongo-spark-connector_2.12;10.4.1 f

+--------------------+--------------------+-------------------+-------------------+--------+----------+--------+-----+------+--------------------+
|                 _id|                body|          closed_at|         created_at|duration|  issue_id|language|stars| state|               title|
+--------------------+--------------------+-------------------+-------------------+--------+----------+--------+-----+------+--------------------+
|67b24e4fd9191f330...|libpcap returned ...|2023-02-08 00:00:00|2023-02-06 00:00:00|       2|1573263352|    Rust|21527|closed|Errors occured wh...|
|67b24e4fd9191f330...|thread 'thread_wr...|2023-02-25 00:00:00|2023-01-05 00:00:00|      51|1520037594|    Rust|21527|closed|thread 'thread_wr...|
|67b24e4fd9191f330...|installing with n...|2023-05-24 00:00:00|2022-12-31 00:00:00|     144|1515053158|    Rust|21527|closed|unable to install...|
|67b24e4fd9191f330...|"Open full report...|2023-02-08 00:00:00|2022-12-22 00:00:00|      48|1507660835|    Rust|21527|

Nombre total d'issues: 63126


+----------------+-----+
|        language|count|
+----------------+-----+
|      JavaScript|28369|
|               C|22401|
|      TypeScript| 3806|
|            Dart| 1785|
|            Rust| 1749|
|             MDX| 1577|
|          Svelte| 1174|
|           Swift|  573|
|             Lua|  521|
|            Java|  470|
|Jupyter Notebook|  388|
|          Python|  235|
|                |   78|
+----------------+-----+

+----------------+------------------+
|        language|      avg_duration|
+----------------+------------------+
|           Swift| 63.97731239092496|
|             MDX| 63.13316423589093|
|            Dart|55.278991596638654|
|Jupyter Notebook|              51.0|
|               C|  48.6522030266506|
|      TypeScript| 47.08328954282712|
|      JavaScript| 37.95424583171772|
|          Python|28.314893617021276|
|            Rust|27.259576901086334|
|          Svelte|23.601362862010223|
|            Java|17.327659574468086|
|             Lua| 10.72552783109405|
|   

In [9]:
import pymongo
import pandas as pd
from collections import Counter
import random

# Connexion à MongoDB
uri = "mongodb://mongodb:27017/"
client = pymongo.MongoClient(uri)
db = client["github_issues"]
collection = db["closed_issues"]

# Charger toutes les issues dans un DataFrame
issues = list(collection.find())
df = pd.DataFrame(issues)

# Analyse du nombre d'issues par langage
df_language_count = df['language'].value_counts().reset_index()
df_language_count.columns = ['language', 'count']
print(df_language_count)



            language  count
0         JavaScript  28369
1                  C  22401
2         TypeScript   3806
3               Dart   1785
4               Rust   1749
5                MDX   1577
6             Svelte   1174
7              Swift    573
8                Lua    521
9               Java    470
10  Jupyter Notebook    388
11            Python    235
12                       78


In [10]:
# Trouver la valeur min et max de duration
min_duration = collection.find_one({}, sort=[("duration", 1)])["duration"]
max_duration = collection.find_one({}, sort=[("duration", -1)])["duration"]

# Compter les occurrences de chaque valeur de duration
duration_counts = collection.aggregate([
    {"$group": {"_id": "$duration", "count": {"$sum": 1}}},
    {"$sort": {"_id": 1}}
])

# Afficher les résultats
print(f"Durée minimale : {min_duration}")
print(f"Durée maximale : {max_duration}")
print("Occurrences de chaque valeur de duration :")
for entry in duration_counts:
    print(f"Durée {entry['_id']}: {entry['count']} fois")

Durée minimale : 0
Durée maximale : 1553
Occurrences de chaque valeur de duration :
Durée 0: 15456 fois
Durée 1: 8462 fois
Durée 2: 3703 fois
Durée 3: 2415 fois
Durée 4: 1793 fois
Durée 5: 1544 fois
Durée 6: 1366 fois
Durée 7: 1190 fois
Durée 8: 1006 fois
Durée 9: 826 fois
Durée 10: 752 fois
Durée 11: 692 fois
Durée 12: 650 fois
Durée 13: 621 fois
Durée 14: 671 fois
Durée 15: 514 fois
Durée 16: 440 fois
Durée 17: 505 fois
Durée 18: 433 fois
Durée 19: 482 fois
Durée 20: 454 fois
Durée 21: 408 fois
Durée 22: 393 fois
Durée 23: 323 fois
Durée 24: 299 fois
Durée 25: 302 fois
Durée 26: 273 fois
Durée 27: 293 fois
Durée 28: 297 fois
Durée 29: 226 fois
Durée 30: 230 fois
Durée 31: 197 fois
Durée 32: 210 fois
Durée 33: 234 fois
Durée 34: 210 fois
Durée 35: 250 fois
Durée 36: 231 fois
Durée 37: 227 fois
Durée 38: 180 fois
Durée 39: 164 fois
Durée 40: 171 fois
Durée 41: 188 fois
Durée 42: 174 fois
Durée 43: 156 fois
Durée 44: 155 fois
Durée 45: 156 fois
Durée 46: 159 fois
Durée 47: 164 fois
Duré

In [11]:
# Définir les intervalles
intervals = [
    (0, 200),
    (201, 400),
    (401, 600),
    (601, 800),
    (801, 1000),
    (1001, 1200),
    (1201, 1400),
    (1401, 1600),
]

# Fonction pour obtenir le numéro d'intervalle
def get_interval_number(duration):
    for i, (start, end) in enumerate(intervals, 1):
        if start <= duration <= end:
            return i
    return None  # Si la durée ne correspond à aucun intervalle

# Mettre à jour les documents pour remplacer la durée par le numéro de l'intervalle
def update_durations():
    cursor = collection.find({"duration": {"$exists": True}})
    
    for issue in cursor:
        duration = issue["duration"]
        interval_number = get_interval_number(duration)
        
        if interval_number:
            collection.update_one(
                {"_id": issue["_id"]},
                {"$set": {"duration": interval_number}}
            )
            print(f"Mis à jour: {issue['_id']}, nouvelle durée: {interval_number}")
        else:
            print(f"Pas de correspondance pour la durée {duration} dans les intervalles définis.")
    
    print("Mise à jour terminée.")

# Appeler la fonction de mise à jour
update_durations()

Mis à jour: 67b24e4fd9191f3304d1f6d0, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6d4, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6d7, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6db, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6de, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6e2, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6e5, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6e9, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6ed, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6f1, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6f6, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f6fb, nouvelle durée: 3
Mis à jour: 67b24e4fd9191f3304d1f6ff, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f705, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f709, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f70e, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f712, nouvelle durée: 1
Mis à jour: 67b24e4fd9191f3304d1f716, nouvelle d

In [29]:
# Extraire les données
cursor = collection.find({"duration": {"$exists": True}})

data = []
for issue in cursor:
    title = issue["title"]
    body = issue["body"]
    language = issue["language"]
    duration = issue["duration"]
    
    # Vous pouvez concaténer le titre et le body pour un meilleur modèle
    text = title + " " + body
    data.append([text, language, duration])

# Convertir en DataFrame
df = pd.DataFrame(data, columns=["text", "language", "duration"])

# Prétraiter les données
# Combiner le titre et le corps en une seule colonne de texte
X = df["text"]
y = df["duration"]

# Vectoriser le texte avec TfidfVectorizer
vectorizer = TfidfVectorizer(max_features=5000)
X_tfidf = vectorizer.fit_transform(X)

# Ajouter la colonne de langue en tant que feature
X_language = pd.get_dummies(df["language"])

# Fusionner les caractéristiques textuelles et celles liées au langage
import scipy.sparse as sp
X_final = sp.hstack([X_tfidf, X_language.values])

# Diviser les données en ensembles d'entraînement et de test
X_train, X_test, y_train, y_test = train_test_split(X_final, y, test_size=0.2, random_state=42)

# Entraîner un modèle de régression logistique
model = LogisticRegression(max_iter=1000)
model.fit(X_train, y_train)

# Prédire sur l'ensemble de test
y_pred = model.predict(X_test)

# Évaluer les résultats
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           1       0.12      0.12      0.12      1568
           2       0.12      0.13      0.13      1530
           3       0.12      0.11      0.11      1619
           4       0.13      0.11      0.12      1605
           5       0.11      0.10      0.10      1578
           6       0.12      0.13      0.13      1619
           7       0.13      0.14      0.14      1581
           8       0.13      0.13      0.13      1526

    accuracy                           0.12     12626
   macro avg       0.12      0.12      0.12     12626
weighted avg       0.12      0.12      0.12     12626



In [31]:
import pandas as pd
from scipy import sparse

# Test example issue
test_example = ["Makefile errors when building with MSYS2", 
                "the error in the makefile seems to be related to the use of  in paths, where msys2 expects unix paths with /.", 
                "C"]

# Preprocess the text of the example
test_text = test_example[0] + " " + test_example[1]  # Combine title and description
test_language = test_example[2]  # Language

# Vectorize the text of the example using the same vectorizer as the training phase
test_tfidf = vectorizer.transform([test_text])

# Convert the language feature into the same format as the training set (one-hot encoding)
test_language_feature = pd.get_dummies([test_language]).reindex(columns=X_language.columns, fill_value=0)

# Convert to a numeric array (integer dtype)
test_language_feature = test_language_feature.values.astype(int)

# Convert to sparse matrix format
test_language_feature_sparse = sparse.csr_matrix(test_language_feature)

# Combine text and language features into a sparse matrix (same as during training)
test_input = sparse.hstack([test_tfidf, test_language_feature_sparse])

# Make a prediction using the trained model
predicted_class = model.predict(test_input)

# Print the predicted class (duration interval)
print(f"The predicted class for this example is: {predicted_class[0]}")


The predicted class for this example is: 2


In [30]:
# Extraire un issue avec la classe de duration égale à 5
issue = collection.find_one({"duration": 5})

# Afficher l'issue
if issue:
    print("Issue trouvé :")
    print(issue)
else:
    print("Aucun issue trouvé avec la classe de duration 5.")

Issue trouvé :
{'_id': ObjectId('67b24e4fd9191f3304d1f6d7'), 'body': 'installing with npcap is a problem on a mac m1 pro. I have tried both cargo and the provided MSI. I have tried both cargo and the provided MSI.', 'closed_at': datetime.datetime(2023, 5, 24, 0, 0), 'created_at': datetime.datetime(2022, 12, 31, 0, 0), 'issue_id': 1515053158, 'language': 'Rust', 'stars': 21527, 'state': 'closed', 'title': 'unable to install on Windows 11 ARM64 VM', 'duration': 5}


In [25]:
# Agrégation pour compter les occurrences de chaque classe de duration
duration_counts = collection.aggregate([
    {"$group": {"_id": "$duration", "count": {"$sum": 1}}},
    {"$sort": {"_id": 1}}  # Tri des résultats par valeur de duration
])

# Afficher les résultats
print("Nombre de documents pour chaque classe de duration :")
for entry in duration_counts:
    print(f"Classe {entry['_id']}: {entry['count']} documents")

Nombre de documents pour chaque classe de duration :
Classe 1: 59235 documents
Classe 2: 2594 documents
Classe 3: 933 documents
Classe 4: 300 documents
Classe 5: 58 documents
Classe 6: 4 documents
Classe 7: 1 documents
Classe 8: 1 documents


In [28]:
# Comptage des documents par classe de duration
duration_counts = collection.aggregate([
    {"$group": {"_id": "$duration", "count": {"$sum": 1}}}
])

# Afficher les classes existantes
existing_classes = {}
for entry in duration_counts:
    existing_classes[entry["_id"]] = entry["count"]

print("Nombre de documents existants pour chaque classe de duration :")
print(existing_classes)

# Déterminer la taille souhaitée pour chaque classe (ici, 8 classes équilibrées)
target_size = max(existing_classes.values())  # Nous prenons la classe la plus grande comme référence
print(f"Taille cible pour chaque classe : {target_size}")

Nombre de documents existants pour chaque classe de duration :
{8: 7861, 3: 7893, 6: 7856, 4: 7926, 1: 7846, 2: 7870, 5: 7840, 7: 8034}
Taille cible pour chaque classe : 8034


In [27]:
# Récupérer tous les documents de la collection
all_documents = list(collection.find({"duration": {"$exists": True}}))

# Répartir les documents par classe de duration
class_to_docs = {}
for doc in all_documents:
    duration = doc["duration"]
    if duration not in class_to_docs:
        class_to_docs[duration] = []
    class_to_docs[duration].append(doc)

# Créer une liste de toutes les classes équilibrées
balanced_classes = []
for duration, docs in class_to_docs.items():
    # Si le nombre de documents pour cette classe est inférieur à la taille cible
    # Ajouter des copies aléatoires de cette classe pour atteindre la taille cible
    while len(docs) < target_size:
        docs.append(random.choice(docs))  # Ajouter un document aléatoire de cette classe

    # Limiter le nombre de documents pour chaque classe à la taille cible
    balanced_classes.extend(docs[:target_size])

# Mettre à jour la base de données avec les nouvelles classes équilibrées
random.shuffle(balanced_classes)  # Mélanger les documents pour ne pas avoir de biais

# Réaffecter les valeurs de 'duration' aux documents
for idx, doc in enumerate(balanced_classes):
    new_class = (idx % 8) + 1  # Créer une classe à partir des classes 1 à 8
    collection.update_one({"_id": doc["_id"]}, {"$set": {"duration": new_class}})

print("Classes de 'duration' équilibrées et réaffectées.")


Classes de 'duration' équilibrées et réaffectées.
